In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from fast_ml.feature_selection import get_constant_features

# Task 1

Task one will focus on combining our individual datasets, getting the combined dataset cleaned, and then preparing the data for the ensuing machine learning tasks. To this end, we will be implementing a train-test split, and then looking for potential correlations in the training set between various continuous/categorical features, and the target death_yn feature. 

In [3]:
#Combining the two datasets and saving as a new csv
df1 = pd.read_csv('covid19-cdc-22207000.csv', keep_default_na=True, delimiter=',', skipinitialspace=True)
df2 = pd.read_csv('covid19-cdc-12468998.csv', keep_default_na=True, delimiter=',', skipinitialspace=True)

combined_df = pd.concat([df1, df2])

combined_df.to_csv('covid19-cdc-combined-22207000-12468998.csv', index=False)

In [4]:
#Reading the new CSV and checking length
df = pd.read_csv('covid19-cdc-combined-22207000-12468998.csv', keep_default_na=True, delimiter=',', skipinitialspace=True)

print(len(df))

40000


# Data Cleaning

In [8]:
#condensing missing data into "Missing" for categorical features
for item in ['case_month', 'res_state','state_fips_code', 'res_county','county_fips_code', 'age_group','sex','race','ethnicity','current_status','symptom_status','hosp_yn','death_yn']:
    df[item] = df[item].replace(np.nan, "Missing")

In [9]:
#adjusting state and county fips code datatypes to categorical, due to finite nature
df["state_fips_code"] = df["state_fips_code"].astype(object)
df["county_fips_code"] = df["county_fips_code"].astype(object)

In [10]:
#checking for duplicate rows
i = 0
for item in df.duplicated(keep=False):
    if item == True:
        print(df.loc[[i]])
    i+=1
    
#There are a fair few duplicate rows in this dataset, though ultimately they are only a small subset of the overall data.
#Becuase the data is not sorted by unique identifiers and consists only of information about each case, these duplicates are
#likely due to similar cirucmstances, rather than errors in data. Furthermore, the large amount of missing data significantly raises the chances of duplicates occuring.
#Therefor, the duplicates will not be deleted

  case_month res_state state_fips_code res_county county_fips_code  age_group  \
0    2022-01        MO            29.0    Missing          Missing  65+ years   

      sex   race            ethnicity  case_positive_specimen_interval  \
0  Female  White  Non-Hispanic/Latino                              0.0   

   case_onset_interval  process exposure_yn             current_status  \
0                  NaN  Missing     Missing  Laboratory-confirmed case   

  symptom_status  hosp_yn   icu_yn death_yn underlying_conditions_yn  
0        Missing  Unknown  Missing      Yes                      NaN  
  case_month res_state state_fips_code res_county county_fips_code  age_group  \
2    2020-03        NY            36.0     QUEENS          36081.0  65+ years   

    sex   race            ethnicity  case_positive_specimen_interval  \
2  Male  Black  Non-Hispanic/Latino                              0.0   

   case_onset_interval  process exposure_yn             current_status  \
2              

    case_month res_state state_fips_code res_county county_fips_code  \
102    2022-02        AZ             4.0   MARICOPA           4013.0   

     age_group     sex   race            ethnicity  \
102  65+ years  Female  White  Non-Hispanic/Latino   

     case_positive_specimen_interval  case_onset_interval  process  \
102                              NaN                  NaN  Missing   

    exposure_yn             current_status symptom_status hosp_yn   icu_yn  \
102     Missing  Laboratory-confirmed case        Missing     Yes  Missing   

    death_yn underlying_conditions_yn  
102      Yes                      NaN  
    case_month res_state state_fips_code   res_county county_fips_code  \
112    2022-01        CA             6.0  LOS ANGELES           6037.0   

     age_group   sex   race        ethnicity  case_positive_specimen_interval  \
112  65+ years  Male  White  Hispanic/Latino                              NaN   

     case_onset_interval  process exposure_yn           

    case_month res_state state_fips_code  res_county county_fips_code  \
240    2021-08        FL            12.0  MIAMI-DADE          12086.0   

          age_group   sex   race            ethnicity  \
240  50 to 64 years  Male  Black  Non-Hispanic/Latino   

     case_positive_specimen_interval  case_onset_interval  process  \
240                              0.0                  NaN  Missing   

    exposure_yn             current_status symptom_status hosp_yn   icu_yn  \
240     Missing  Laboratory-confirmed case        Missing     Yes  Missing   

    death_yn underlying_conditions_yn  
240      Yes                      NaN  
    case_month res_state state_fips_code  res_county county_fips_code  \
242    2021-01        RI            44.0  PROVIDENCE          44007.0   

     age_group     sex   race            ethnicity  \
242  65+ years  Female  White  Non-Hispanic/Latino   

     case_positive_specimen_interval  case_onset_interval  process  \
242                              N

    case_month res_state state_fips_code  res_county county_fips_code  \
288    2020-07        FL            12.0  MIAMI-DADE          12086.0   

     age_group   sex   race        ethnicity  case_positive_specimen_interval  \
288  65+ years  Male  White  Hispanic/Latino                              NaN   

     case_onset_interval  process exposure_yn             current_status  \
288                  NaN  Missing     Missing  Laboratory-confirmed case   

    symptom_status  hosp_yn   icu_yn death_yn underlying_conditions_yn  
288        Missing  Missing  Missing      Yes                      NaN  
    case_month res_state state_fips_code res_county county_fips_code  \
291    2020-12        IL            17.0     DUPAGE          17043.0   

     age_group     sex   race            ethnicity  \
291  65+ years  Female  White  Non-Hispanic/Latino   

     case_positive_specimen_interval  case_onset_interval  process  \
291                              NaN                  0.0  Missing 

    case_month res_state state_fips_code  res_county county_fips_code  \
382    2020-11        NM            35.0  BERNALILLO          35001.0   

     age_group   sex   race        ethnicity  case_positive_specimen_interval  \
382  65+ years  Male  White  Hispanic/Latino                              NaN   

     case_onset_interval  process exposure_yn             current_status  \
382                  NaN  Missing     Missing  Laboratory-confirmed case   

    symptom_status hosp_yn   icu_yn death_yn underlying_conditions_yn  
382        Missing     Yes  Missing      Yes                      NaN  
    case_month res_state state_fips_code res_county county_fips_code  \
383    2020-04        MA            25.0  MIDDLESEX          25017.0   

     age_group     sex   race            ethnicity  \
383  65+ years  Female  White  Non-Hispanic/Latino   

     case_positive_specimen_interval  case_onset_interval  process  \
383                              0.0                  NaN  Missing   

...

      case_month res_state state_fips_code   res_county county_fips_code  \
38544    2021-12        NY            36.0  WESTCHESTER          36119.0   

            age_group     sex     race ethnicity  \
38544  50 to 64 years  Female  Unknown   Unknown   

       case_positive_specimen_interval  case_onset_interval  process  \
38544                              NaN                  NaN  Missing   

      exposure_yn             current_status symptom_status  hosp_yn   icu_yn  \
38544     Missing  Laboratory-confirmed case        Missing  Missing  Missing   

      death_yn underlying_conditions_yn  
38544       No                      NaN  
      case_month res_state state_fips_code res_county county_fips_code  \
38549    2022-01        NY            36.0   ROCKLAND          36087.0   

          age_group   sex     race ethnicity  case_positive_specimen_interval  \
38549  0 - 17 years  Male  Unknown   Unknown                              NaN   

       case_onset_interval  process ex

      case_month res_state state_fips_code       res_county county_fips_code  \
38828    2022-05        MD            24.0  PRINCE GEORGE'S          24033.0   

            age_group     sex   race ethnicity  \
38828  50 to 64 years  Female  Black   Missing   

       case_positive_specimen_interval  case_onset_interval  process  \
38828                              NaN                  NaN  Missing   

      exposure_yn             current_status symptom_status hosp_yn   icu_yn  \
38828     Missing  Laboratory-confirmed case        Missing      No  Missing   

      death_yn underlying_conditions_yn  
38828       No                      NaN  
      case_month res_state state_fips_code res_county county_fips_code  \
38835    2022-05        OH            39.0     MEDINA          39103.0   

            age_group   sex   race            ethnicity  \
38835  18 to 49 years  Male  White  Non-Hispanic/Latino   

       case_positive_specimen_interval  case_onset_interval  process  \
38835   

      case_month res_state state_fips_code res_county county_fips_code  \
39220    2020-11        NY            36.0   ROCKLAND          36087.0   

            age_group   sex     race ethnicity  \
39220  18 to 49 years  Male  Unknown   Unknown   

       case_positive_specimen_interval  case_onset_interval  process  \
39220                              0.0                  NaN  Missing   

      exposure_yn             current_status symptom_status  hosp_yn   icu_yn  \
39220     Missing  Laboratory-confirmed case        Missing  Missing  Missing   

      death_yn underlying_conditions_yn  
39220       No                      NaN  
      case_month res_state state_fips_code res_county county_fips_code  \
39239    2022-08        NY            36.0     NASSAU          36059.0   

       age_group     sex     race ethnicity  case_positive_specimen_interval  \
39239  65+ years  Female  Unknown   Unknown                              NaN   

       case_onset_interval  process exposure_yn 

      case_month res_state state_fips_code res_county county_fips_code  \
39623    2020-12        ID            16.0        ADA          16001.0   

            age_group   sex   race            ethnicity  \
39623  50 to 64 years  Male  White  Non-Hispanic/Latino   

       case_positive_specimen_interval  case_onset_interval  process  \
39623                              0.0                  NaN  Missing   

      exposure_yn             current_status symptom_status hosp_yn   icu_yn  \
39623     Missing  Laboratory-confirmed case        Unknown      No  Missing   

      death_yn underlying_conditions_yn  
39623       No                      NaN  
      case_month res_state state_fips_code  res_county county_fips_code  \
39624    2020-11        NH            33.0  ROCKINGHAM          33015.0   

       age_group   sex   race            ethnicity  \
39624  65+ years  Male  White  Non-Hispanic/Latino   

       case_positive_specimen_interval  case_onset_interval  process  \
39624     

      case_month res_state state_fips_code res_county county_fips_code  \
39908    2021-08        TX            48.0     HARRIS          48201.0   

            age_group   sex     race ethnicity  \
39908  18 to 49 years  Male  Missing   Missing   

       case_positive_specimen_interval  case_onset_interval  process  \
39908                              NaN                  NaN  Missing   

      exposure_yn             current_status symptom_status hosp_yn   icu_yn  \
39908     Missing  Laboratory-confirmed case        Missing      No  Missing   

      death_yn underlying_conditions_yn  
39908       No                      NaN  
      case_month res_state state_fips_code res_county county_fips_code  \
39926    2022-01        TX            48.0    TARRANT          48439.0   

            age_group   sex   race        ethnicity  \
39926  18 to 49 years  Male  White  Hispanic/Latino   

       case_positive_specimen_interval  case_onset_interval  process  \
39926                       